In [14]:
import numpy as np
import math
import random
class Node:
    def __init__(self,numtheta):
        self.theta=[0.0]*numtheta
        self.downstream=None
        self.upstream=None
        self.output=None
        self.deljthetabydelthetaunit = [0.0]*numtheta
        self.deljthetabydelnet = None
def loadtheta(network,theta ):
    for i in range(len(network)):
        for j in range(len(network[i])):
            for k in range(len(network[i][j].theta)):
                network[i][j].theta[k] = theta[i][j][k]
    return network
def sigmoid(x):
    return (1.0/(1.0+math.exp(-x)))
def forwardpass(features, network):
    for i in range(len(network)):
        for j in range(len(network[i])):
            tempnode = network[i][j]
            temp=0.0
            if(i==0):
                #parse from input
                for k in range(len(tempnode.theta)):
                    if(k==len(tempnode.theta)-1):
                        temp += tempnode.theta[k] * 1.0
                    else:
                        temp += tempnode.theta[k] * features[k]
                
            else:
                #parse from last layer
                prevlayer = network[i-1]
                for k in range(len(tempnode.theta)):
                    if(k==len(tempnode.theta)-1):
                        temp += tempnode.theta[k] * 1.0
                    else:
                        temp += tempnode.theta[k] * prevlayer[k].output
            tempnode.output = sigmoid(temp)
    lastlayer = network[len(network)-1]
    templist=[]
    for i in range(len(lastlayer)):
        templist.append(lastlayer[i].output)
    return templist
def findcost(output, correctoutput):
    temp = 0.0
    for i in range(len(output)):
        temp += 0.5 * ((output[i]-correctoutput[i])**2)
    return temp
def findtotalcostarr(inparr,outarr,network):
    costarr=[]
    for i in range(len(inparr)):
        tempforwardpass= forwardpass(inparr[i],network)
        print("tempforwardpass is")
        print(tempforwardpass)
        tempcost = findcost(tempforwardpass,outarr[i])
        costarr.append(tempcost)
    avgcost=0.0
    for i in range(len(costarr)):
        avgcost += costarr[i]
    avgcost = avgcost/(len(costarr))
    return costarr, avgcost
def printdeljtheta(network):
    print("deljtheta is")
    templist=[]
    for i in range(len(network)):
        templist.append([])
        for j in range(len(network[i])):
            templist[i].append([])
            for k in range(len(network[i][j].theta)):
                templist[i][j].append(network[i][j].deljthetabydelthetaunit[k])
    print(templist)
    return
def neuralnet(inparr, outarr, hiddeninfo,learningrate, batchsize,costthres, sampletheta):
    numtrain = len(inparr)
    diminput= len(inparr[0])
    dimoutput = len(outarr[0])
    network=[]
    for i in range(len(hiddeninfo)):
        network.append([])
    network.append([])
    for i in range(len(hiddeninfo)):
        #i is layer iterator
        for j in range(hiddeninfo[i]):
            #j is sublayer num unit iterator
            if(i==0):
                tempnode = Node(diminput+1)
                network[i].append(tempnode)
            else:
                tempnode = Node(hiddeninfo[i-1]+1)
                network[i].append(tempnode)
            
    #add output layer
    for i in range(dimoutput):
        tempnode = Node(hiddeninfo[len(hiddeninfo)-1] + 1)
        network[len(network)-1].append(tempnode)
    #load theta for testing
#     network = loadtheta(network, sampletheta)
    #necessary forwardpass
#     tempforwardpass = forwardpass(inparr[0],network)
#     print(tempforwardpass)
#     #lets see cost
#     print("cost = "+str(findcost(tempforwardpass,outarr[0])))
    
    #time for backprop
    deljthetabydelthetamat=[]
    for i in range(len(network)):
        deljthetabydelthetamat.append([])
        for j in range(len(network[i])):
            deljthetabydelthetamat[i].append([])
            for k in range(len(network[i][j].theta)):
                deljthetabydelthetamat[i][j].append(0.0)
    print("simulated deljtheata")
    print(deljthetabydelthetamat)
    print("real deljtheta")
    printdeljtheta(network)
    subbatchiter=0
    batchcount=0
    numwholedatapass=0
    numiter=0
    costarr,oldavgcost = findtotalcostarr(inparr,outarr,network)
    shufflehelper = []
    for i in range(len(inparr)):
    	shufflehelper.append(i)
    while(0==0):
        numiter+=1
        print("numiter is")
        print(numiter)
        print("numwholedata pass is")
        print(numwholedatapass)
        ioindex = batchsize*batchcount+subbatchiter
        print("ioindex is "+str(ioindex))
        tempforwardpass = forwardpass(inparr[shufflehelper[ioindex]],network)
        for i in range(len(network)-1,-1,-1):
            #lets calculate deljtheta by del netj
            for j in range(len(network[i])):
                tempnode = network[i][j]
                if(i==len(network)-1):
                    tempnode.deljthetabydelnet = -1.0*(outarr[shufflehelper[ioindex]][j]-tempnode.output)*(tempnode.output)*(1.0-tempnode.output)
                else:
                    temp=0.0
                    nextlayer = network[i+1]
                    for k in range(len(nextlayer)):
                        temp += nextlayer[k].deljthetabydelnet * nextlayer[k].theta[j]
                    tempnode.deljthetabydelnet = (tempnode.output) * (1.0- tempnode.output) * temp
                if(i==0):
                    #ok is input
                    for k in range(len(tempnode.theta)):
                        if(k==len(tempnode.theta)-1):
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * 1.0
                        else:
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * inparr[shufflehelper[ioindex]][k]
                else:
                    prevlayer = network[i-1]
                    for k in range(len(tempnode.theta)):
                        if(k==len(tempnode.theta)-1):
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * 1.0
                        else:
                            tempnode.deljthetabydelthetaunit[k] = tempnode.deljthetabydelnet * prevlayer[k].output
        subbatchiter+=1
        for i in range(len(network)):
                for j in range(len(network[i])):
                    for k in range(len(network[i][j].theta)):
                        deljthetabydelthetamat[i][j][k] += network[i][j].deljthetabydelthetaunit[k]
        print("simulated deljtheata")
        print(deljthetabydelthetamat)
        print("real deljtheta")
        printdeljtheta(network)
        if(subbatchiter==batchsize):
            print("batch over")
            for i in range(len(network)):
                for j in range(len(network[i])):
                    for k in range(len(network[i][j].theta)):
                        network[i][j].theta[k] = network[i][j].theta[k] - learningrate * deljthetabydelthetamat[i][j][k]/(1.0*batchsize)
                        deljthetabydelthetamat[i][j][k]=0.0
            #set deljthetabydel zero
            
            
            
            subbatchiter=0
            batchcount+=1
            if(len(inparr)==batchcount*batchsize):
                print("shuffle the shufflehelper")
                numwholedatapass+=1
                batchcount=0
                random.shuffle(shufflehelper)

                costarr, newavgcost=findtotalcostarr(inparr,outarr,network)
                
                print("cost is")
                print(newavgcost)
                if(newavgcost<costthres):
                    print("cost is lower")
                    break
                elif(numwholedatapass>=20000):
                    break
                else:
                    #do nothing continue
                    oldavgcost=newavgcost
                
        
            
            
            
#         tempforwardpass = forwardpass(inparr[0],network)
#         print(tempforwardpass)
#         #lets see cost
#         print("cost = "+str(findcost(tempforwardpass,outarr[0])))        
    
    return network
# sampleinparr = [[0.05, 0.10]]
sampleinparr = [[0.0, 1.0],[1.0,0.0],[0.0,0.0],[1.0,1.0]]

# sampleoutput = [[0.01, 0.99]]
sampleoutput = [[0.99],[0.99],[0.01],[0.99]]
samplehiddeninfo = [1]
samplelearningrate=0.5
sampletheta = [[[.15,.20,.35],[.25,.30,.35]],[[.40,.45,.60],[.50,.55,.60]]]

samplenetwork = neuralnet(sampleinparr,sampleoutput,samplehiddeninfo,samplelearningrate,1, pow(10,-4),sampletheta)
print(samplenetwork)
            
                
    


simulated deljtheata
[[[0.0, 0.0, 0.0]], [[0.0, 0.0]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0]], [[0.0, 0.0]]]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
tempforwardpass is
[0.5]
numiter is
1
numwholedata pass is
0
ioindex is 0
simulated deljtheata
[[[0.0, 0.0, 0.0]], [[-0.06125, -0.1225]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0]], [[-0.06125, -0.1225]]]
batch over
numiter is
2
numwholedata pass is
0
ioindex is 1
simulated deljtheata
[[[-0.0008999526745774703, 0.0, -0.0008999526745774703]], [[-0.05877241956424296, -0.11754483912848591]]]
real deljtheta
deljtheta is
[[[-0.0008999526745774703, -0.0, -0.0008999526745774703]], [[-0.05877241956424296, -0.11754483912848591]]]
batch over
numiter is
3
numwholedata pass is
0
ioindex is 2
simulated deljtheata
[[[0.0, 0.0, 0.0019671725094653632]], [[0.0655749219768084, 0.13112034342817463]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0019671725094653632]], [[0.0655749219768084, 0.13112034342817463]]]
ba

real deljtheta
deljtheta is
[[[-0.005447475206751172, -0.0, -0.005447475206751172]], [[-0.027426386277041446, -0.05088283338569502]]]
batch over
numiter is
120
numwholedata pass is
29
ioindex is 3
simulated deljtheata
[[[-0.005207324294332875, -0.005207324294332875, -0.005207324294332875]], [[-0.02752556793848323, -0.04791515214501766]]]
real deljtheta
deljtheta is
[[[-0.005207324294332875, -0.005207324294332875, -0.005207324294332875]], [[-0.02752556793848323, -0.04791515214501766]]]
batch over
shuffle the shufflehelper
tempforwardpass is
[0.7437965980125867]
tempforwardpass is
[0.7438115427684722]
tempforwardpass is
[0.7407165572003721]
tempforwardpass is
[0.7468318206584171]
cost is
0.08928779025441007
numiter is
121
numwholedata pass is
30
ioindex is 0
simulated deljtheata
[[[-0.005338123979857013, 0.0, -0.005338123979857013]], [[-0.02541057441334145, -0.0469126708200859]]]
real deljtheta
deljtheta is
[[[-0.005338123979857013, -0.0, -0.005338123979857013]], [[-0.02541057441334145, 

batch over
shuffle the shufflehelper
tempforwardpass is
[0.7545649964720521]
tempforwardpass is
[0.7545716147244863]
tempforwardpass is
[0.7468479514721779]
tempforwardpass is
[0.761817855592952]
cost is
0.08823352001182304
numiter is
229
numwholedata pass is
57
ioindex is 0
simulated deljtheata
[[[-0.005444666677543496, -0.005444666677543496, -0.005444666677543496]], [[-0.02660255412097572, -0.04140397195190967]]]
real deljtheta
deljtheta is
[[[-0.005444666677543496, -0.005444666677543496, -0.005444666677543496]], [[-0.02660255412097572, -0.04140397195190967]]]
batch over
numiter is
230
numwholedata pass is
57
ioindex is 1
simulated deljtheata
[[[0.0, 0.0, 0.020264256903845167]], [[0.06946924316773673, 0.13836837098516044]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.020264256903845167]], [[0.06946924316773673, 0.13836837098516044]]]
batch over
numiter is
231
numwholedata pass is
57
ioindex is 2
simulated deljtheata
[[[-0.006361009689233466, 0.0, -0.006361009689233466]], [[-0.02698956

84
ioindex is 0
simulated deljtheata
[[[-0.005917914263240843, -0.005917914263240843, -0.005917914263240843]], [[-0.0278505442712993, -0.03938434232027732]]]
real deljtheta
deljtheta is
[[[-0.005917914263240843, -0.005917914263240843, -0.005917914263240843]], [[-0.0278505442712993, -0.03938434232027732]]]
batch over
numiter is
338
numwholedata pass is
84
ioindex is 1
simulated deljtheata
[[[-0.007394795890505986, 0.0, -0.007394795890505986]], [[-0.025332026057436192, -0.041853315624559524]]]
real deljtheta
deljtheta is
[[[-0.007394795890505986, -0.0, -0.007394795890505986]], [[-0.025332026057436192, -0.041853315624559524]]]
batch over
numiter is
339
numwholedata pass is
84
ioindex is 2
simulated deljtheata
[[[0.0, -0.00723447468451841, -0.00723447468451841]], [[-0.024401294846579206, -0.04027703431589413]]]
real deljtheta
deljtheta is
[[[-0.0, -0.00723447468451841, -0.00723447468451841]], [[-0.024401294846579206, -0.04027703431589413]]]
batch over
numiter is
340
numwholedata pass is
84

[[[-0.006939215057720974, -0.006939215057720974, -0.006939215057720974]], [[-0.03258043265768933, -0.042593414464737564]]]
real deljtheta
deljtheta is
[[[-0.006939215057720974, -0.006939215057720974, -0.006939215057720974]], [[-0.03258043265768933, -0.042593414464737564]]]
batch over
numiter is
447
numwholedata pass is
111
ioindex is 2
simulated deljtheata
[[[0.0, -0.010317158214471971, -0.010317158214471971]], [[-0.030115951501502848, -0.04791280606363367]]]
real deljtheta
deljtheta is
[[[-0.0, -0.010317158214471971, -0.010317158214471971]], [[-0.030115951501502848, -0.04791280606363367]]]
batch over
numiter is
448
numwholedata pass is
111
ioindex is 3
simulated deljtheata
[[[-0.010018600558224585, 0.0, -0.010018600558224585]], [[-0.028889454320726215, -0.04585385016912515]]]
real deljtheta
deljtheta is
[[[-0.010018600558224585, -0.0, -0.010018600558224585]], [[-0.028889454320726215, -0.04585385016912515]]]
batch over
shuffle the shufflehelper
tempforwardpass is
[0.753601437252342]
te

...

batch over
numiter is
16806
numwholedata pass is
4201
ioindex is 1
simulated deljtheata
[[[0.0, -0.0001767465389330415, -0.0001767465389330415]], [[-0.00023721455564719107, -0.0002599920698028514]]]
real deljtheta
deljtheta is
[[[-0.0, -0.0001767465389330415, -0.0001767465389330415]], [[-0.00023721455564719107, -0.0002599920698028514]]]
batch over
numiter is
16807
numwholedata pass is
4201
ioindex is 2
simulated deljtheata
[[[0.0, 0.0, 0.000436696433383001]], [[5.5319349272854315e-05, 0.0007702719027189324]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.000436696433383001]], [[5.5319349272854315e-05, 0.0007702719027189324]]]
batch over
numiter is
16808
numwholedata pass is
4201
ioindex is 3
simulated deljtheata
[[[-4.19792812709072e-08, -4.19792812709072e-08, -4.19792812709072e-08]], [[-6.924585122426296e-06, -6.9295245505903115e-06]]]
real deljtheta
deljtheta is
[[[-4.19792812709072e-08, -4.19792812709072e-08, -4.19792812709072e-08]], [[-6.924585122426296e-06, -6.9295245505903115e-06]]]

real deljtheta
deljtheta is
[[[0.0, 0.0, 0.00043166805683758413]], [[5.462790980742117e-05, 0.0007617504878825851]]]
batch over
numiter is
16952
numwholedata pass is
4237
ioindex is 3
simulated deljtheata
[[[0.0, -0.00017512883531891894, -0.00017512883531891894]], [[-0.00023514973903043123, -0.0002576956776673408]]]
real deljtheta
deljtheta is
[[[-0.0, -0.00017512883531891894, -0.00017512883531891894]], [[-0.00023514973903043123, -0.0002576956776673408]]]
batch over
shuffle the shufflehelper
tempforwardpass is
[0.9780226869364846]
tempforwardpass is
[0.9780222873954525]
tempforwardpass is
[0.033505771633716]
tempforwardpass is
[0.9893777945598043]
cost is
0.00010497875839560102
numiter is
16953
numwholedata pass is
4238
ioindex is 0
simulated deljtheata
[[[0.0, -0.00017493499581795613, -0.00017493499581795613]], [[-0.0002349237614160544, -0.00025744408922497155]]]
real deljtheta
deljtheta is
[[[-0.0, -0.00017493499581795613, -0.00017493499581795613]], [[-0.0002349237614160544, -0.00025

tempforwardpass is
[0.033357658117093424]
tempforwardpass is
[0.9894122122901436]
cost is
0.0001036276688189642
numiter is
17097
numwholedata pass is
4274
ioindex is 0
simulated deljtheata
[[[-3.700970554872197e-08, -3.700970554872197e-08, -3.700970554872197e-08]], [[-6.1531328599129595e-06, -6.157479754241484e-06]]]
real deljtheta
deljtheta is
[[[-3.700970554872197e-08, -3.700970554872197e-08, -3.700970554872197e-08]], [[-6.1531328599129595e-06, -6.157479754241484e-06]]]
batch over
numiter is
17098
numwholedata pass is
4274
ioindex is 1
simulated deljtheata
[[[0.0, 0.0, 0.0004266096964385571]], [[5.393317181367455e-05, 0.0007531716959831156]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0004266096964385571]], [[5.393317181367455e-05, 0.0007531716959831156]]]
batch over
numiter is
17099
numwholedata pass is
4274
ioindex is 2
simulated deljtheata
[[[-0.00017336014123734575, 0.0, -0.00017336014123734575]], [[-0.00023290789754186047, -0.00025520296122454256]]]
real deljtheta
deljtheta is
[

numwholedata pass is
4310
ioindex is 1
simulated deljtheata
[[[0.0, -0.0001712149296575086, -0.0001712149296575086]], [[-0.00023022261558125424, -0.00025221876667547405]]]
real deljtheta
deljtheta is
[[[-0.0, -0.0001712149296575086, -0.0001712149296575086]], [[-0.00023022261558125424, -0.00025221876667547405]]]
batch over
numiter is
17243
numwholedata pass is
4310
ioindex is 2
simulated deljtheata
[[[-0.00017108065477937007, 0.0, -0.00017108065477937007]], [[-0.00023005135355744235, -0.00025202984440370296]]]
real deljtheta
deljtheta is
[[[-0.00017108065477937007, -0.0, -0.00017108065477937007]], [[-0.00023005135355744235, -0.00025202984440370296]]]
batch over
numiter is
17244
numwholedata pass is
4310
ioindex is 3
simulated deljtheata
[[[0.0, 0.0, 0.0004224355430702535]], [[5.3352354894689245e-05, 0.0007459387276649114]]]
real deljtheta
deljtheta is
[[[0.0, 0.0, 0.0004224355430702535]], [[5.3352354894689245e-05, 0.0007459387276649114]]]
batch over
shuffle the shufflehelper
tempforward

numiter is
17388
numwholedata pass is
4346
ioindex is 3
simulated deljtheata
[[[-0.0001695620075816212, 0.0, -0.0001695620075816212]], [[-0.00022811013843979815, -0.0002498720122410261]]]
real deljtheta
deljtheta is
[[[-0.0001695620075816212, -0.0, -0.0001695620075816212]], [[-0.00022811013843979815, -0.0002498720122410261]]]
batch over
shuffle the shufflehelper
tempforwardpass is
[0.9782617529074533]
tempforwardpass is
[0.9782613793244183]
tempforwardpass is
[0.03306375395957941]
tempforwardpass is
[0.989480479248824]
cost is
0.00010097353858622409
numiter is
17389
numwholedata pass is
4347
ioindex is 0
simulated deljtheata
[[[-3.2249496997189183e-08, -3.2249496997189183e-08, -3.2249496997189183e-08]], [[-5.403837913846678e-06, -5.4076189917353505e-06]]]
real deljtheta
deljtheta is
[[[-3.2249496997189183e-08, -3.2249496997189183e-08, -3.2249496997189183e-08]], [[-5.403837913846678e-06, -5.4076189917353505e-06]]]
batch over
numiter is
17390
numwholedata pass is
4347
ioindex is 1
simula

In [ ]:
pow(10,-3)